In [1]:
import torch 
from torch import nn

import ray
from ray.rllib.agents import ppo
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.utils.annotations import override

#from models import VisualEncoder
from train import *
from wrappers_2 import *

/root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
class VisualEncoder(nn.Module):
    def __init__(self):
        super().__init__()

        self.cnn = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=8, stride=4, padding=0),  
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=4, stride=2, padding=0), 
            nn.ReLU(),
            nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=0), 
            nn.ReLU(),
            nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=0),
            nn.ReLU(), 
            nn.Conv2d(64, 512, kernel_size=2, stride=1, padding=0),
            nn.ReLU(),
            nn.Flatten(),
        )

    def forward(self, x):
        return self.cnn(x)

In [3]:
from torch.nn.functional import one_hot

class MyModelClass(TorchModelV2, nn.Module):
    def __init__(self, obs_space, action_space, num_outputs, model_config, name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs, model_config, name)
        nn.Module.__init__(self)
        visual_features_dim = 512
        target_features_dim = 9 * 11 * 11 
        self.visual_encoder = VisualEncoder()
        self.visual_encoder.load_state_dict(
            torch.load("/IGLU-Minecraft/models/AnnaCNN/encoder_weigths.pth", map_location=torch.device('cpu'))
        )
        self.target_encoder = nn.Sequential(
            nn.Conv3d(7, 1, kernel_size=1, stride=1, padding=0),
            nn.ELU(),
        )
        policy_hidden_dim = 256 
        self.policy_network = nn.Sequential(
            nn.Linear(visual_features_dim + target_features_dim, policy_hidden_dim),
            nn.ELU(),
            nn.Linear(policy_hidden_dim, policy_hidden_dim),
            nn.ELU(),
            nn.Linear(policy_hidden_dim, policy_hidden_dim),
            nn.ELU()
        )
        self.action_head = nn.Linear(policy_hidden_dim, action_space.n)
        self.value_head = nn.Linear(policy_hidden_dim, 1)
        self.last_value = None
        
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.visual_encoder.cuda()
            self.target_encoder.cuda()
            self.policy_network.cuda()
            self.action_head.cuda()
            self.value_head.cuda()
        
    @override(TorchModelV2)
    def forward(self, input_dict, state, seq_lens):
        obs = input_dict['obs']
        pov = obs['pov'].permute(0, 3, 1, 2).float() / 255.0
        target = one_hot(obs['target_grid'].long(), num_classes=7).permute(0, 4, 1, 2, 3).float()
        if self.use_cuda:
            pov.cuda()
            target.cuda()
            
        visual_features = self.visual_encoder(pov)
        target_features = self.target_encoder(target)
        target_features = target_features.reshape(target_features.shape[0], -1)
        features = torch.cat([visual_features, target_features], dim=1)
        features = self.policy_network(features)
        action = self.action_head(features)
        self.last_value = self.value_head(features).squeeze(1)
        return action, state
    
    @override(TorchModelV2)
    def value_function(self):
        assert self.last_value is not None, "must call forward() first"
        return self.last_value

In [4]:
ModelCatalog.register_custom_model("my_torch_model", MyModelClass)

In [5]:
class VisualObservationWrapper(ObsWrapper):
    def __init__(self, env, include_target=False):
        super().__init__(env)
        self.observation_space = {   
            'pov': gym.spaces.Box(low=0, high=255, shape=(64, 64, 3)),
            'inventory': gym.spaces.Box(low=0.0, high=20.0, shape=(6,)),
            'compass': gym.spaces.Box(low=-180.0, high=180.0, shape=(1,))
        }
        if include_target:
            self.observation_space['target_grid'] = \
                gym.spaces.Box(low=0, high=6, shape=(9, 11, 11))
        self.observation_space = gym.spaces.Dict(self.observation_space)

    def observation(self, obs, reward=None, done=None, info=None):
        if info is not None:
            if 'target_grid' in info:
                target_grid = info['target_grid']
                del info['target_grid']
            else:
                logger.error(f'info: {info}')
                if hasattr(self.unwrapped, 'should_reset'):
                    self.unwrapped.should_reset(True)
                target_grid = self.env.unwrapped.tasks.current.target_grid
        else:
            target_grid = self.env.unwrapped.tasks.current.target_grid
        return {
            'pov': obs['pov'].astype(np.float32),
            'inventory': obs['inventory'],
            'compass': np.array([obs['compass']['angle'].item()]),
            'target_grid': target_grid
        }

In [6]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="0"

class RewardWrapper(gym.RewardWrapper):
    def __init__(self, env):
        super().__init__(env)
    
    def reward(self, rew):
        if rew == 0:
            rew = -0.1
        return rew
    
def env_creator(env_config):
    env = gym.make('IGLUSilentBuilder-v0', max_steps=1000)
    env.update_taskset(TaskSet(preset=['C32']))
    #env = PovOnlyWrapper(env)
    env = VisualObservationWrapper(env, include_target=True)
    env = SelectAndPlace(env)
    env = Discretization(env, flat_action_space('human-level'))
    env = RewardWrapper(env)
    return env

from ray.tune.registry import register_env
register_env("my_env", env_creator)

from ray import tune
from ray.rllib.agents.ppo import PPOTrainer

In [7]:
from ray.tune.integration.wandb import WandbLogger

analysis = tune.run(PPOTrainer, 
         config={
             "env": "my_env", 
             "framework": "torch",
             "num_gpus": 1,
             "num_workers": 1,
             "sgd_minibatch_size": 256,
             "clip_param": 0.2,
             "entropy_coeff": 0.01,
             "lambda": 0.95,
             "train_batch_size": 1000,
             #"gamma": 0.99,
             "model": {
                    # Specify our custom model from above.
                    "custom_model": "my_torch_model",
                    # Extra kwargs to be passed to your model's c'tor.
                    "custom_model_config": {},
              },
             "logger_config": {
                  "wandb": {
                      "project": "IGLU-Minecraft",
                      "name": "PPO MultiTask (C32) pretrained (AnnaCNN) (3 noops after placement) r: -0.1"
                  }
              }

        },
        loggers=[WandbLogger])

/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/_private/services.py:238: UserWarning: Not all Ray Dashboard dependencies were found. To use the dashboard please install Ray using `pip install ray[default]`. To disable this message, set RAY_DISABLE_IMPORT_WARNING env var to '1'.
  warnings.warn(warning_message)


2021-10-21 19:45:11,244	INFO wandb.py:170 -- Already logged into W&B.
2021-10-21 19:45:11,329	ERROR syncer.py:72 -- Log sync requires rsync to be installed.
wandb: Currently logged in as: linar (use `wandb login --relogin` to force relogin)
wandb: WARNING Tried to auto resume run with id 0b57e_00000 but id 67041_00000 is set.
wandb: wandb version 0.12.5 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
(pid=188) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=188)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


(pid=188) 2021-10-21 19:45:14,919	INFO ppo.py:159 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(pid=188) 2021-10-21 19:45:14,920	INFO trainer.py:728 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=186) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=186)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=188) 2021-10-21 19:45:21,025	WARNING util.py:55 -- Install gputil for GPU system monitoring.
(pid=186) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=186)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=186) /root/miniconda/envs/py37/lib/python3.7/site-packages/gy

Result for PPO_my_env_67041_00000:
  agent_timesteps_total: 1000
  custom_metrics: {}
  date: 2021-10-21_19-46-24
  done: false
  episode_len_mean: 431.0
  episode_media: {}
  episode_reward_max: -41.900000000000325
  episode_reward_mean: -44.50000000000032
  episode_reward_min: -47.100000000000314
  episodes_this_iter: 2
  episodes_total: 2
  experiment_id: a63f200b87524df7b0bab0d758dab5c9
  hostname: 97fec18c88ee
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.870019210709466
          entropy_coeff: 0.009999999999999998
          kl: 0.008355930164915317
          policy_loss: 0.11407052204012871
          total_loss: 0.44816574309435153
          vf_explained_var: 0.17857752740383148
          vf_loss: 0.3611242252919409
    num_agent_steps_sampled: 1000
    num_agent_steps_trained: 1000
    num_steps_sampled: 1000
    num_steps_trained: 1000
  iterations_since

Result for PPO_my_env_67041_00000:
  agent_timesteps_total: 2000
  custom_metrics: {}
  date: 2021-10-21_19-46-45
  done: false
  episode_len_mean: 437.25
  episode_media: {}
  episode_reward_max: -41.900000000000325
  episode_reward_mean: -44.42500000000034
  episode_reward_min: -47.100000000000314
  episodes_this_iter: 2
  episodes_total: 4
  experiment_id: a63f200b87524df7b0bab0d758dab5c9
  hostname: 97fec18c88ee
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.8584622250662908
          entropy_coeff: 0.009999999999999998
          kl: 0.011583619312315207
          policy_loss: -0.0317104760143492
          total_loss: 0.19593507125973703
          vf_explained_var: 0.2962351143360138
          vf_loss: 0.2539134434527821
    num_agent_steps_sampled: 2000
    num_agent_steps_trained: 2000
    num_steps_sampled: 2000
    num_steps_trained: 2000
  iterations_sinc

...

Result for PPO_my_env_67041_00000:
  agent_timesteps_total: 1824000
  custom_metrics: {}
  date: 2021-10-22_09-00-29
  done: false
  episode_len_mean: 254.11
  episode_media: {}
  episode_reward_max: -20.200000000000017
  episode_reward_mean: -25.41100000000009
  episode_reward_min: -66.00000000000053
  episodes_this_iter: 4
  episodes_total: 5762
  experiment_id: a63f200b87524df7b0bab0d758dab5c9
  hostname: 97fec18c88ee
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 5.014237059495043e-47
          cur_lr: 5.000000000000001e-05
          entropy: 0.43674585587448544
          entropy_coeff: 0.009999999999999998
          kl: 0.011917428854852434
          policy_loss: -0.05845870218343205
          total_loss: 0.6991290907065074
          vf_explained_var: 0.661958634853363
          vf_loss: 0.7619552473227184
    num_agent_steps_sampled: 1824000
    num_agent_steps_trained: 1824000
    num_steps_sampled: 1824000
    num_steps_trained: 182400

Result for PPO_my_env_67041_00000:
  agent_timesteps_total: 1825000
  custom_metrics: {}
  date: 2021-10-22_09-01-07
  done: false
  episode_len_mean: 254.64
  episode_media: {}
  episode_reward_max: -20.200000000000017
  episode_reward_mean: -25.46400000000009
  episode_reward_min: -66.00000000000053
  episodes_this_iter: 5
  episodes_total: 5767
  experiment_id: a63f200b87524df7b0bab0d758dab5c9
  hostname: 97fec18c88ee
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 5.014237059495043e-47
          cur_lr: 5.000000000000001e-05
          entropy: 0.30271101577414405
          entropy_coeff: 0.009999999999999998
          kl: 0.03131255075928214
          policy_loss: -0.07390906603799927
          total_loss: 0.6569002111752827
          vf_explained_var: 0.6959981918334961
          vf_loss: 0.7338363852765825
    num_agent_steps_sampled: 1825000
    num_agent_steps_trained: 1825000
    num_steps_sampled: 1825000
    num_steps_trained: 182500

2021-10-22 09:01:37,174	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-22 09:01:37,174	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-22 09:01:37,235	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
Process _WandbLoggingProcess-1:
Traceback (most recent call last):
  File "/root/miniconda/envs/py37/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/integration/wandb.py", line 200, in

Traceback (most recent call last):
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ipython-7.25.0-py3.7.egg/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_76/3010183041.py", line 29, in <module>
    loggers=[WandbLogger])
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/tune.py", line 532, in run
    runner.step()
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/trial_runner.py", line 554, in step
    self._process_events(timeout=timeout)  # blocking
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/trial_runner.py", line 675, in _process_events
    timeout=timeout)  # blocking
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/ray_trial_executor.py", line 718, in get_next_available_trial
    ready, _ = ray.wait(shuffled_results, timeout=timeout)
  File "/root/miniconda/envs/py37/lib/python3.7/site-pac

TypeError: object of type 'NoneType' has no len()